## Data preprocessing 食譜資料前處理

### Import neccessary libraries and packages 導入必要套件

In [1]:
import matplotlib
import pandas as pd
import numpy as np
import json
import pymongo
import jieba
import string
import re
import os
import time
import random
import googletrans
import nltk
from IPython.display import clear_output
clear_output(wait=True)
from nltk.stem.lancaster import LancasterStemmer
from collections import Counter
pd.set_option('display.max_columns', 110)
import matplotlib.pyplot as plt
from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator

### Connecting to mongoDB 資料庫連線

In [2]:
# Create connnect 建立與mongoDB連線
client = pymongo.MongoClient(host='192.168.158.128', port=27017)

In [3]:
# assign database 選擇資料庫
db = client.tibame
# assign colection 選擇collection
collection = db.recipe_raw

In [4]:
# Query specific column from all recipe_raw 選擇要讀取的資料欄位
queryArgs = {}
projectField = {'_id' : True, 'url' : True, 'title' : True, 'author' : True, 'ingredient' : True, 'steps' : True, 'category' : True}
search_response = db.recipe_raw.find(queryArgs, projection=projectField)

In [5]:
recipe_list = []
for item in search_response:
    recipe_list.append(item)

In [6]:
# total recipe numbers 確認資料總數
len(recipe_list)

58392

# 設定辭典 : 
<!--     選用辭典
    辭典內容調整(切詞、刪除...) -->

In [7]:
# 開啟 stop word list
stop_word = []
with open('./jieba_data/stopword.txt', 'r', encoding='utf-8') as file:
    txt = file.readlines()
# 過濾掉 txt內的\n
    stop_word = [each.strip('\n') for each in txt]
# 開啟 自定義辭典    
with open('./jieba_data/mydict.txt', 'r', encoding='utf-8') as file:
    txt = file.readlines()
# 過濾 權重、詞性、空白
    word_bank = [element.replace(' 10 n','').replace(' 20 n','').strip('\n') for element in txt]

# 讀取辭典
jieba.load_userdict('./jieba_data/mydict.txt')
# 將 嫩、豆腐 確實切開 
jieba.suggest_freq(('嫩', '豆腐'), True)
for word in word_bank:
# 確保 辭典內容 確實保留
    jieba.suggest_freq(word, True)
# 刪除辭典字
jieba.del_word('雞胸肉')
jieba.del_word('雞肉')
jieba.del_word('蛋黃')
jieba.del_word('全蛋')
jieba.del_word('雞蛋')
jieba.del_word('雞胸肉片')

Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\BIGDAT~1\AppData\Local\Temp\jieba.cache
Loading model cost 0.749 seconds.
Prefix dict has been built successfully.


In [8]:
# Initial googletrans instance
translator = googletrans.Translator()
word_bank_en = {}
for word in word_bank:
    word_bank_en[word] = (translator.translate(word)).text.lower()
# word_bank_en

In [9]:
def clear():
    os.system('clear')

In [10]:
word_list = []
total_match = []

for n, recipe in enumerate(recipe_list):
# 食物向量    
    food_vector = {}
    try:
        ingredient_step = recipe['ingredient'] + ',' + recipe['steps']
        
        url = recipe['url'];
        title = recipe['title']
        author = recipe['author'];
        category = recipe['category']
        
        print('食譜編號: ', n)
        seg = jieba.cut(ingredient_step, cut_all = False)
#         print('結巴斷詞後: ', seg)
#         word_list = word_list + ([item for item in list(seg) if len(item) > 0])
        matched = set(seg).intersection(set(word_bank))
        
        if len(matched) > 4:
            for each_word in word_bank_en:
                if each_word in list(matched):
                    food_vector[word_bank_en[each_word]] = 1
                else:
                    food_vector[word_bank_en[each_word]] = 0

            # forming recipe record
            vector_dict = {}

            vector_dict['url'] = url
            vector_dict['title'] = title
            vector_dict['author'] = author
            vector_dict['vector'] = food_vector
            vector_dict['category'] = category
#             print(vector_dict)
#             save back to mongoDB
            db = client.tibame
            collection = db.recipe_vector_5
            insert_item = vector_dict
            insert_result = db.recipe_vector_5.insert_one(insert_item)


            print(insert_result)
            clear()
        else:
            print('The recipe is not good....')
            clear()
            pass
        
        total_match = total_match + list(matched)
    except:
        pass
    
# total_match

食譜編號:  0
食譜編號:  1
The recipe is not good....
食譜編號:  2
食譜編號:  3
食譜編號:  4
The recipe is not good....
食譜編號:  5
食譜編號:  6
The recipe is not good....
食譜編號:  7
The recipe is not good....
食譜編號:  8
The recipe is not good....
食譜編號:  9
The recipe is not good....
食譜編號:  10
The recipe is not good....
食譜編號:  11
The recipe is not good....
食譜編號:  12
The recipe is not good....
食譜編號:  13
The recipe is not good....
食譜編號:  14
食譜編號:  15
The recipe is not good....
食譜編號:  16
The recipe is not good....
食譜編號:  17
食譜編號:  18
The recipe is not good....
食譜編號:  19
食譜編號:  20
食譜編號:  21
食譜編號:  22
The recipe is not good....
食譜編號:  23
The recipe is not good....
食譜編號:  24
食譜編號:  25
The recipe is not good....
食譜編號:  26
The recipe is not good....
食譜編號:  27
The recipe is not good....
食譜編號:  28
The recipe is not good....
食譜編號:  29
The recipe is not good....
食譜編號:  30
The recipe is not good....
食譜編號:  31
The recipe is not good....
食譜編號:  32
食譜編號:  33
The recipe is not good....
食譜編號:  34
The recipe is not good....
食譜編號:  35
Th

食譜編號:  204
The recipe is not good....
食譜編號:  205
The recipe is not good....
食譜編號:  206
The recipe is not good....
食譜編號:  207
The recipe is not good....
食譜編號:  208
The recipe is not good....
食譜編號:  209
The recipe is not good....
食譜編號:  210
The recipe is not good....
食譜編號:  211
The recipe is not good....
食譜編號:  212
The recipe is not good....
食譜編號:  213
The recipe is not good....
食譜編號:  214
The recipe is not good....
食譜編號:  215
食譜編號:  216
食譜編號:  217
The recipe is not good....
食譜編號:  218
The recipe is not good....
食譜編號:  219
The recipe is not good....
食譜編號:  220
The recipe is not good....
食譜編號:  221
The recipe is not good....
食譜編號:  222
The recipe is not good....
食譜編號:  223
食譜編號:  224
The recipe is not good....
食譜編號:  225
The recipe is not good....
食譜編號:  226
The recipe is not good....
食譜編號:  227
The recipe is not good....
食譜編號:  228
The recipe is not good....
食譜編號:  229
The recipe is not good....
食譜編號:  230
The recipe is not good....
食譜編號:  231
The recipe is not good....
食譜編號:  232
The re

食譜編號:  407
食譜編號:  408
The recipe is not good....
食譜編號:  409
The recipe is not good....
食譜編號:  410
The recipe is not good....
食譜編號:  411
The recipe is not good....
食譜編號:  412
食譜編號:  413
The recipe is not good....
食譜編號:  414
The recipe is not good....
食譜編號:  415
The recipe is not good....
食譜編號:  416
食譜編號:  417
The recipe is not good....
食譜編號:  418
The recipe is not good....
食譜編號:  419
The recipe is not good....
食譜編號:  420
食譜編號:  421
The recipe is not good....
食譜編號:  422
The recipe is not good....
食譜編號:  423
The recipe is not good....
食譜編號:  424
The recipe is not good....
食譜編號:  425
The recipe is not good....
食譜編號:  426
The recipe is not good....
食譜編號:  427
The recipe is not good....
食譜編號:  428
The recipe is not good....
食譜編號:  429
The recipe is not good....
食譜編號:  430
食譜編號:  431
The recipe is not good....
食譜編號:  432
The recipe is not good....
食譜編號:  433
The recipe is not good....
食譜編號:  434
The recipe is not good....
食譜編號:  435
The recipe is not good....
食譜編號:  436
食譜編號:  437
The recipe 

食譜編號:  606
The recipe is not good....
食譜編號:  607
The recipe is not good....
食譜編號:  608
The recipe is not good....
食譜編號:  609
The recipe is not good....
食譜編號:  610
The recipe is not good....
食譜編號:  611
The recipe is not good....
食譜編號:  612
The recipe is not good....
食譜編號:  613
The recipe is not good....
食譜編號:  614
The recipe is not good....
食譜編號:  615
The recipe is not good....
食譜編號:  616
The recipe is not good....
食譜編號:  617
The recipe is not good....
食譜編號:  618
The recipe is not good....
食譜編號:  619
The recipe is not good....
食譜編號:  620
The recipe is not good....
食譜編號:  621
The recipe is not good....
食譜編號:  622
The recipe is not good....
食譜編號:  623
The recipe is not good....
食譜編號:  624
The recipe is not good....
食譜編號:  625
The recipe is not good....
食譜編號:  626
The recipe is not good....
食譜編號:  627
The recipe is not good....
食譜編號:  628
The recipe is not good....
食譜編號:  629
The recipe is not good....
食譜編號:  630
The recipe is not good....
食譜編號:  631
The recipe is not good....
食譜編號:  632
T

食譜編號:  844
The recipe is not good....
食譜編號:  845
The recipe is not good....
食譜編號:  846
The recipe is not good....
食譜編號:  847
The recipe is not good....
食譜編號:  848
食譜編號:  849
The recipe is not good....
食譜編號:  850
The recipe is not good....
食譜編號:  851
The recipe is not good....
食譜編號:  852
The recipe is not good....
食譜編號:  853
食譜編號:  854
食譜編號:  855
The recipe is not good....
食譜編號:  856
The recipe is not good....
食譜編號:  857
The recipe is not good....
食譜編號:  858
The recipe is not good....
食譜編號:  859
The recipe is not good....
食譜編號:  860
The recipe is not good....
食譜編號:  861
The recipe is not good....
食譜編號:  862
食譜編號:  863
The recipe is not good....
食譜編號:  864
The recipe is not good....
食譜編號:  865
The recipe is not good....
食譜編號:  866
The recipe is not good....
食譜編號:  867
The recipe is not good....
食譜編號:  868
The recipe is not good....
食譜編號:  869
The recipe is not good....
食譜編號:  870
The recipe is not good....
食譜編號:  871
The recipe is not good....
食譜編號:  872
食譜編號:  873
The recipe is not good

...

食譜編號:  57539
The recipe is not good....
食譜編號:  57540
The recipe is not good....
食譜編號:  57541
The recipe is not good....
食譜編號:  57542
The recipe is not good....
食譜編號:  57543
The recipe is not good....
食譜編號:  57544
The recipe is not good....
食譜編號:  57545
The recipe is not good....
食譜編號:  57546
The recipe is not good....
食譜編號:  57547
The recipe is not good....
食譜編號:  57548
The recipe is not good....
食譜編號:  57549
The recipe is not good....
食譜編號:  57550
The recipe is not good....
食譜編號:  57551
The recipe is not good....
食譜編號:  57552
The recipe is not good....
食譜編號:  57553
The recipe is not good....
食譜編號:  57554
The recipe is not good....
食譜編號:  57555
The recipe is not good....
食譜編號:  57556
The recipe is not good....
食譜編號:  57557
The recipe is not good....
食譜編號:  57558
The recipe is not good....
食譜編號:  57559
The recipe is not good....
食譜編號:  57560
The recipe is not good....
食譜編號:  57561
The recipe is not good....
食譜編號:  57562
The recipe is not good....
食譜編號:  57563
The recipe is not good....


食譜編號:  57753
The recipe is not good....
食譜編號:  57754
The recipe is not good....
食譜編號:  57755
The recipe is not good....
食譜編號:  57756
The recipe is not good....
食譜編號:  57757
The recipe is not good....
食譜編號:  57758
The recipe is not good....
食譜編號:  57759
The recipe is not good....
食譜編號:  57760
The recipe is not good....
食譜編號:  57761
The recipe is not good....
食譜編號:  57762
The recipe is not good....
食譜編號:  57763
The recipe is not good....
食譜編號:  57764
The recipe is not good....
食譜編號:  57765
The recipe is not good....
食譜編號:  57766
The recipe is not good....
食譜編號:  57767
The recipe is not good....
食譜編號:  57768
The recipe is not good....
食譜編號:  57769
The recipe is not good....
食譜編號:  57770
The recipe is not good....
食譜編號:  57771
The recipe is not good....
食譜編號:  57772
The recipe is not good....
食譜編號:  57773
The recipe is not good....
食譜編號:  57774
The recipe is not good....
食譜編號:  57775
The recipe is not good....
食譜編號:  57776
The recipe is not good....
食譜編號:  57777
The recipe is not good....


食譜編號:  57966
The recipe is not good....
食譜編號:  57967
The recipe is not good....
食譜編號:  57968
The recipe is not good....
食譜編號:  57969
The recipe is not good....
食譜編號:  57970
The recipe is not good....
食譜編號:  57971
The recipe is not good....
食譜編號:  57972
The recipe is not good....
食譜編號:  57973
The recipe is not good....
食譜編號:  57974
The recipe is not good....
食譜編號:  57975
The recipe is not good....
食譜編號:  57976
The recipe is not good....
食譜編號:  57977
The recipe is not good....
食譜編號:  57978
The recipe is not good....
食譜編號:  57979
The recipe is not good....
食譜編號:  57980
The recipe is not good....
食譜編號:  57981
The recipe is not good....
食譜編號:  57982
The recipe is not good....
食譜編號:  57983
The recipe is not good....
食譜編號:  57984
The recipe is not good....
食譜編號:  57985
The recipe is not good....
食譜編號:  57986
The recipe is not good....
食譜編號:  57987
The recipe is not good....
食譜編號:  57988
The recipe is not good....
食譜編號:  57989
The recipe is not good....
食譜編號:  57990
The recipe is not good....


The recipe is not good....
食譜編號:  58176
The recipe is not good....
食譜編號:  58177
The recipe is not good....
食譜編號:  58178
The recipe is not good....
食譜編號:  58179
The recipe is not good....
食譜編號:  58180
The recipe is not good....
食譜編號:  58181
The recipe is not good....
食譜編號:  58182
The recipe is not good....
食譜編號:  58183
The recipe is not good....
食譜編號:  58184
The recipe is not good....
食譜編號:  58185
The recipe is not good....
食譜編號:  58186
The recipe is not good....
食譜編號:  58187
The recipe is not good....
食譜編號:  58188
The recipe is not good....
食譜編號:  58189
The recipe is not good....
食譜編號:  58190
The recipe is not good....
食譜編號:  58191
The recipe is not good....
食譜編號:  58192
The recipe is not good....
食譜編號:  58193
The recipe is not good....
食譜編號:  58194
The recipe is not good....
食譜編號:  58195
The recipe is not good....
食譜編號:  58196
The recipe is not good....
食譜編號:  58197
The recipe is not good....
食譜編號:  58198
The recipe is not good....
食譜編號:  58199
The recipe is not good....
食譜編號:  58200


食譜編號:  58387
The recipe is not good....
食譜編號:  58388
The recipe is not good....
食譜編號:  58389
The recipe is not good....
食譜編號:  58390
The recipe is not good....
食譜編號:  58391
The recipe is not good....


In [ ]:
ingredient_freq_list = sorted(total_match , key = lambda x : total_match[1], reverse=True)
ingredient_freq_list

## 以下是胡亂練習用的

### Translate vector features word-bank  把向量詞庫先翻譯

In [ ]:
translator = googletrans.Translator()

word_bank_en = []
with open('./jieba_data/mydict.txt', 'r', encoding='utf-8') as file:
    txt = file.readlines()
    word_bank_list = [each.strip('\n') for each in txt]
    for each in word_bank_list:
        translated_result = translator.translate(each)
        output_str = translated_result.text.lower()+'\n'
        with open('./jieba_data/word_bank_en.txt', 'a', encoding='utf-8') as f:
            f.write(output_str)
    

### 解決單複數及時態變形

In [ ]:
word_bank_dict = {}
with open('./jieba_data/word_bank_en.txt', 'r', encoding='utf-8') as file:
    txt = file.readlines()
    for each in txt:
        word_bank_dict[each.strip('\n')] = 0 

In [ ]:
word_bank_dict

### Extracting ingredient and steps 擷取食譜內食材及步驟字串

In [ ]:
# Initial googletrans instance
translator = googletrans.Translator()

for each_recipe in recipe_list[:20]:   ## 先練習前五筆
    
    try:    
        ingre_step = each_recipe['ingredient'] + ',' + each_recipe['steps']
    except:
        continue
    #print(ingre_step)
    #print('------------------  Translated and segmented -------------------')
    
    
    # Translate into EN
    translated_results = translator.translate(ingre_step)
    no_punctuation_result = translated_results.text.translate(str.maketrans('', '', string.punctuation))
    ingre_step_list = no_punctuation_result.split()
    print(ingre_step_list)
    print('================== Find intersection ===========================')
    # find matched items by using set. 用集合的交集方式找出配對的食材跟做法 ##效果不好 
    
    # Try nltk, put all words back into stem state
    # initial a PorterStemmer() instance
    stemmer = nltk.PorterStemmer()
    original_matched_vec = set([word.lower() for word in ingre_step_list]).intersection(set(word_bank_dict.keys()))
    stem_matched_vec = set([stemmer.stem(word.lower()) for word in ingre_step_list]).intersection(set(word_bank_dict.keys()))
    union_set = original_matched_vec.union(stem_matched_vec)
    #print(matched_vec)
    
    # If maintain recipes with more than 3 elements
    if len(union_set) > 3:
        food_vector = {}
        for key in word_bank_dict:
            if key in union_set:
                food_vector[key] = 1
            else:
                food_vector[key] = 0
        print(food_vector)

        vector_dict = {}
        url = each_recipe['url']; author = each_recipe['author']; category = each_recipe['category']
        vector_dict['url'] = url
        vector_dict['author'] = author
        vector_dict['vector'] = food_vector
        vector_dict['category'] = category

        db = client.tibame
        collection = db.recipe_vector
        insert_item = vector_dict
        insert_result = db.recipe_vector.insert_one(insert_item)
        print(insert_result)
    
    print("********************** Next one ********************************")
    time.sleep(random.randrange(15,17))

## !!!!!!! 用正規表示法段文字 !!!!!!!!!!!!!!!!!!!!!!!

In [ ]:
recipe_list[5]['ingredient']

## 設定結巴字典及段字權重

In [ ]:
# count the frequency of each word
seg_counter = Counter(total_match)

In [ ]:
# transfer the object into dictionary type
counter_dict = dict(seg_counter)
counter_dict

In [ ]:
# Sorting the word based on its frequency, from highest to lowest
ingredient_freq_list = sorted(counter_dict.keys(), key = lambda x : counter_dict[x], reverse=True)
ingredient_freq_list

## 算總辭頻

In [ ]:
stop_word = []
with open('./jieba_data/stopword.txt', 'r', encoding='utf-8') as file:
    txt = file.readlines()
    stop_word = [each.strip('\n') for each in txt]
    
with open('./jieba_data/mydict.txt', 'r', encoding='utf-8') as file:
    txt = file.readlines()
    word_bank = [element.replace(' 10 n','').replace(' 20 n','').strip('\n') for element in txt]

    
    
    
    
jieba.load_userdict('./jieba_data/mydict.txt')
jieba.suggest_freq(('嫩', '豆腐'), True)
for word in word_bank:
    jieba.suggest_freq(word, True)

jieba.del_word('雞胸肉')
jieba.del_word('雞肉')
jieba.del_word('蛋黃')
jieba.del_word('全蛋')
jieba.del_word('雞蛋')
jieba.del_word('雞胸肉片')    



total_list = []
ingredient = ''
for recipe in recipe_list[:1000]:
    try:
        ingredient = recipe['ingredient']
        seg = jieba.cut(ingredient, cut_all = False)
        ingredient_list = [item for item in list(seg) if item not in stop_word]
        total_list = total_list + ingredient_list
            
    except:
        pass

In [ ]:
total_list

In [ ]:
# count the frequency of each word
seg_counter = Counter(total_list)

In [ ]:
# transfer the object into dictionary type
counter_dict = dict(seg_counter)
counter_dict

In [ ]:
# Sorting the word based on its frequency, from highest to lowest
ingredient_freq_list = sorted(counter_dict , key = lambda x : counter_dict[x], reverse=True)
ingredient_freq_list

In [ ]:
# Initial googletrans instance
translator = googletrans.Translator()

# initial a PorterStemmer() instance
stemmer = nltk.PorterStemmer()

In [ ]:
ingredient = recipe_list[0]['ingredient']
ingredient

In [ ]:
ingredient_en = translator.translate(ingredient)
ingredient_en.text

In [ ]:
#remove space and stem each word
ingredient_list = [item.strip() for item in ingredient_en.text.split(',')]
ingredient_list

In [ ]:
pattern = list(word_bank_dict.keys())
pattern

In [ ]:
matches = set(ingredient_list).intersection(set(pattern))

In [ ]:
matches

### Translate CN to EN 中翻英

### Strings segmentation 斷字

### Matching to form recipe vector 配對成特徵向量

### Save processed recipe vector back to mongoDB 轉換好的資料存回資料庫（另開新的collection）